In [24]:
import numpy as np
class board:
    def __init__(self,obsticles,m=18,n=9):
        self.m=m
        self.n=n
        self.pg=[]
        self.obsticles=obsticles
        self.dots=np.ones([m,n])
    def copy(self):
        e=board(self.obsticles.copy(),self.m,self.n)
        # print(len(self.pg))
        # e.add_pg(self.pg[0].copy())
        # e.add_pg(self.pg[1].copy())
        # e.add_pg(self.pg[2].copy())
        e.pg=[i.copy() for i in self.pg]
        for i in range(len(e.pg)):
            # print('board copy called')
            e.pg[i].index=i
            e.pg[i].enviroment=e
        e.dots=self.dots.copy()
        return e
    def utility(self):
        gain=self.pg[0].score-self.dots.sum()+self.m*self.n
        return gain
    def add_pg(self,pg):
        self.pg.append(pg)
    def request_move(self,w,index):
        flag=False
        print(index)
        pg=self.pg[index]
        next=np.array([pg.x,pg.y])
        if w==0  and pg.y<self.n-1:
            next=np.array([pg.x,pg.y+1])
        elif w==1  and pg.x<self.m-1:
            next=np.array([pg.x+1,pg.y])
        elif w==2  and pg.y>0:
            next=np.array([pg.x,pg.y-1])
        elif w==3 and pg.x>0 :
            next=np.array([pg.x-1,pg.y])
        if not((self.obsticles==next).all(axis=1)).any():
            if not (next[0],next[1])==(pg.x,pg.y):
                flag=True
            pg.x,pg.y=next[0],next[1]
        if index==0 and flag:
            pg.score=pg.score-1
            if self.dots[next[0],next[1]]==1:
                self.dots[next[0],next[1]]=0
                pg.score=pg.score+10   
    def Map(self):
        b=np.zeros([self.m,self.n],dtype=np.int8)
        for i in self.pg:
            b[i.x,i.y]=2
        b[self.pg[0].x,self.pg[0].y]=1
        b[self.obsticles[:,0],self.obsticles[:,1]]=-1
        return b 
    def is_leaf(self):
        cond=(self.pg[0].x,self.pg[0].y==self.pg[1].x,self.pg[1].y) or (self.pg[0].x,self.pg[0].y==self.pg[2].x,self.pg[2].y) or self.dots.sum()==np.shape(self.obs)[0]
        return cond 
    def step(self):
        for i in range(len(self.pg)):
             self.pg[i].go()          
        

In [25]:
class PG:
    def __init__(self,x,y,enviroment):
        self.x=x
        self.y=y
        self.enviroment=enviroment
        enviroment.add_pg(self)
        self.index=len(enviroment.pg)-1
        print(self.index,'index of a pg added')
    def move(self,w):
        self.enviroment.request_move(w,self.index)



In [31]:
class Pacman(PG):
    max_depth=5
    def __init__(self, x, y, enviroment=None):
        super().__init__(x, y, enviroment)
        self.score=0
        self.enviroment.dots[x,y]=0
        self.enviroment.pg
    def copy(self):
        print('pacman copy')
        a =Pacman(self.x,self.y,self.enviroment)
        a.enviroment.pg.pop()
        a.score=self.score
        a.enviroment.dots=self.enviroment.dots.copy()
        return a
    def decsision(self):
        b=self.enviroment
        max_i,i=self.Max_search(b)
        return i
    def Max_search(self,b0,depth=0):
        l=[]
        if depth<Pacman.max_depth:
            for i in range(4):
                b=b0.copy()
                b.pg[0].move(i)
                l.append(b.pg[0].Min_search(b,depth+1))
            return max(l),np.argmax(l)
        else:
            b=b0.copy()
            return b.utility()
    def Min_search(self,b0,depth):
        l=[]
        if depth<Pacman.max_depth and self.enviroment.is_leaf():
            for j in range(4):
                for k in range(4):
                    b=b0.copy()
                    b.pg[1].move(j)
                    b.pg[2].move(k)
                    l.append(b.pg[0].Max_search(b,depth+1)[0])
            return min(l)
        else:
            b=b0.copy()
            return b.utility()
    def go(self):
        i=self.decsision()
        self.move(i)

In [27]:
class ghost(PG):
    def __init__(self, x, y, enviroment):
        super().__init__(x, y, enviroment)
    def go(self):
        self.move(np.random.choice(4))
    def copy(self):
        a =ghost(self.x,self.y,self.enviroment)
        a.enviroment.pg.pop()
        # print("ghost copy")
        return a


In [32]:
from pandas import read_csv as read
r=read('dots.csv')
r=np.array(r)
m=18
n=9
k=4
obs=r[0:56]
b=board(obs,m,n)
p=Pacman(r[55,0],r[55,1],b)
g1=ghost(r[57,0],r[57,1],b)
g2=ghost(r[56,0],r[56,1],b)

0 index of a pg added
1 index of a pg added
2 index of a pg added


In [34]:
b.step()
b.Map()

pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
1
2
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
1
2
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of

array([[ 0,  0,  0,  0,  0,  0,  0,  0,  0],
       [ 0, -1, -1, -1,  0, -1, -1, -1,  0],
       [ 0, -1,  0,  0,  0,  0,  0, -1,  0],
       [ 0,  0,  0, -1,  0, -1,  0,  0,  0],
       [-1, -1,  0, -1,  0, -1,  0, -1, -1],
       [ 0,  0,  0,  0,  0,  0,  0,  0,  0],
       [ 0, -1,  0, -1, -1, -1,  0, -1,  0],
       [ 2, -1,  0, -1,  0, -1,  0, -1,  0],
       [ 0, -1,  0, -1,  0,  0,  0, -1,  0],
       [ 0, -1,  2, -1,  0,  0,  0, -1,  0],
       [ 0, -1,  0, -1,  0, -1,  0, -1,  0],
       [ 0, -1,  0, -1, -1, -1,  0, -1,  0],
       [ 0,  0,  0,  0,  0,  0,  0,  0,  0],
       [-1, -1,  0, -1,  0, -1,  0, -1, -1],
       [ 0,  0,  0,  0,  0,  0,  0,  0,  0],
       [ 0, -1,  0,  0,  0,  0,  0, -1,  0],
       [ 0,  0,  0, -1,  0, -1,  0,  0,  0],
       [ 0, -1, -1, -1,  0, -1, -1, -1,  1]], dtype=int8)

In [36]:
p.decsision()

pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
1
2
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
1
2
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
0
pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added
pacman copy
3 index of a pg added
3 index of

3

In [19]:
b.copy()

pacman copy
3 index of a pg added
3 index of a pg added
3 index of a pg added


In [21]:
# p.move(1)
a=b.copy()
a.pg[0].x=0
print(a.pg[0].x)
print(b.pg[0].x)
q=p.copy()
print(q.x)

6
pacman copy
ghost copy
ghost copy
board copy called
board copy called
board copy called
0
17
pacman copy
17


In [14]:
a.pg[0].x=2
print(a.pg[0].x)
print(b.pg[0].x)

2
17


In [95]:

def random_place(m,n,k):
    index_array1 = np.arange(m)
    index_array2 = np.arange(n)
    np.random.shuffle(index_array1)
    np.random.shuffle(index_array2)
    x,y=index_array1[0:k],index_array2[0:k]
    x=np.concatenate((x,y)).reshape((k,2))
   
    return x
    # def sucssesor(self,l):
    #     b=self.enviroment.copy()
    #     pg=b.pg
    #     for i in range(1,5):
    #         pg[0].move(i)
    #         for j in range(1,5):
    #             pg[1].move(j)
    #             for k in range(1,5):
    #                 pg[2].move(k)
    #                 l.append(b.Map())
    #                 pg[1].move((i+2)%4+1)
    #                 pg[2].move((i+2)%4+1)
    #         pg[0].move((i+2)%4+1)

0

In [ ]:
import copy
class a():
    def __init__(self,x) -> None:
        self.x=x
        self.l=[B(x,self), B(x,self)]
    def f(self,r):
        if a.s>r:
            print('hello')
    def __copy__(self):
        q=a(copy.copy(self.x))
        q.l=[copy.copy(i) for i in self.l]
        # for i in q.l:
        #     i.y=q
        return q
        
class B():
    def __init__(self,x,y) -> None:
        self.x=x
        self.y=y
    def f(self,r):
        if a.s>r:
            print('hello')
    def __copy__(self):

        e=B(copy.copy(self.x),copy.copy(self.y))
        return e
x=a(5)
y=copy.copy(x)
y.l[0].x=10
print(y.l[0].x)
print(x.l[0].x)

: 

In [24]:
q=p.copy()
q.enviroment.obsticles[0,0]=10
print(p.enviroment.obsticles[0,0])
print(q.enviroment.obsticles[0,0])

pacman copy
10
10


In [4]:
er=[1,2,3,55]
er.pop()
er

[1, 2, 3]